In [ ]:
from google.colab import drive
drive.mount('/content/gdrive',force_remount=True)
%cd /content/gdrive/MyDrive

Mounted at /content/gdrive
/content/gdrive/MyDrive


In [ ]:
!pip install keras_preprocessing

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.6/42.6 kB 2.4 MB/s eta 0:00:00


In [ ]:
import string
import numpy as np
from PIL import Image
import os
from pickle import dump, load
import numpy as np
from keras.applications.xception import Xception, preprocess_input
from tensorflow.keras.utils import load_img , img_to_array

from keras.preprocessing.text import Tokenizer
from keras_preprocessing.sequence import pad_sequences
from keras.utils import to_categorical
from tensorflow.keras.layers import Add
from keras.models import Model, load_model
from keras.layers import Input, Dense, LSTM, Embedding, Dropout
# small library for seeing the progress of loops.
from tqdm import tqdm_notebook as tqdm
tqdm().pandas()

<ipython-input-8-3a09d7937e55>:18: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  tqdm().pandas()


0it [00:00, ?it/s]

In [ ]:
%cd IA

/content/gdrive/MyDrive/IA


In [ ]:
# Loading a text file into memory
def load_doc(filename):
    # Opening the file as read only
    file = open(filename, 'r', encoding='utf-8')
    all_text = file.read()
    file.close()
    return all_text

    

# get all imgs with their captions
def all_img_captions(filename):
    cpts = {}
    #loop through lines
    for line in filename.split('\n'): # each line contains image name & its caption separated by tab
        #split by tabs
        img_cpt = line.split('\t')
        if len(img_cpt) < 2: continue
        img, cpt = img_cpt
        #remove image extension & index (remove everything befor the dot)
        img_name = img.split('.')[0]
        #add to dictionary
        if img_name not in cpts:
            cpts[img_name] = [cpt]
        else:
            cpts[img_name].append(cpt)
    return cpts
#Data cleaning- lower casing, removing puntuations and words containing numbers
def cleaning_text(captions):
    table = str.maketrans('','',string.punctuation)
    for img,caps in captions.items():
        for i,img_caption in enumerate(caps):
            img_caption.replace("-"," ")
            desc = img_caption.split()
            #converts to lowercase
            desc = [word.lower() for word in desc]
            #remove punctuation from each token
            desc = [word.translate(table) for word in desc]
            #remove hanging 's and a 
            desc = [word for word in desc if(len(word)>1)]
            #remove tokens with numbers in them
            desc = [word for word in desc if(word.isalpha())]
            #convert back to string
            img_caption = ' '.join(desc)
            captions[img][i]= img_caption
    return captions
def text_vocabulary(descriptions):
    # build vocabulary of all unique words
    vocab = set()
    for key in descriptions.keys():
        [vocab.update(d.split()) for d in descriptions[key]]
    return vocab
#All descriptions in one file 
def save_descriptions(descriptions, filename):
    lines = list()
    for key, desc_list in descriptions.items():
        for desc in desc_list:
            lines.append(key + '\t' + desc )
    data = "\n".join(lines)
    file = open(filename,"w")
    file.write(data)
    file.close()
# Set these path according to project folder in you system
dataset_text = "Flickr8k_text"
dataset_images = "Flicker8k_Dataset"
#we prepare our text data
filename = dataset_text + "/" + "Flickr8k.arabic.full.txt"
#loading the file that contains all data
#mapping them into descriptions dictionary img to 5 captions
captions_file_text = load_doc(filename)

descriptions = all_img_captions(captions_file_text)
subset = {k:descriptions[k] for k in list(descriptions.keys())[:10]}
print(subset)
print("Length of descriptions =" ,len(descriptions))
#cleaning the descriptions
import string

clean_descriptions = cleaning_text(descriptions)
#building vocabulary 
vocabulary = text_vocabulary(clean_descriptions)
print("Length of vocabulary = ", len(vocabulary))
#saving each description to file 
save_descriptions(clean_descriptions, "descriptions.txt")

{'1000268201_693b08cb0e': ['طفلة صغيرة تتسلق إلى مسرح خشبي', 'طفلة صغيرة تتسلق الدرج إلى منزلها', 'فتاة صغيرة في ثوب وردي تذهب إلى المقصورة الخشبية'], '1001773457_577c3a7d70': ['كلب أسود وكلب ثلاثي الألوان يلعبان مع بعضهما البعض على الطريق', 'كلب أسود وكلب أبيض ببقع بنية يحدقان في بعضهما البعض في الشارع', 'كلاب على الرصيف تتحرك نحو بعضها البعض'], '1002674143_1b742ab4b8': ['فتاة صغيرة مغطاة بالطلاء تجلس أمام قوس قزح', 'فتاة صغيرة تجلس أمام قوس قزح ملون كبير', 'فتاة أمام لوحة قوس قزح'], '1003163366_44323f5815': ['رجل يجلس على مقعد بينما يجلس كلبه بجانبه', 'رجل ينام على مقعد في الخارج مع كلب أبيض وأسود يجلس بجانبه', 'رجل بلا قميص يجلس على مقعد في الحديقة مع كلبه'], '1007129816_e794419615': ['رجل يرتدي قبعة برتقالية', 'رجل يرتدي قبعة برتقالية ونظارات', 'الرجل ذو الأذن المثقوبة يرتدي نظارات وقبعة برتقالية اللون'], '1007320043_627395c3d8': ['طفل يلعب على حبل', 'فتاة صغيرة تتسلق على الحبل الأحمر', 'طفل صغير يمسك بالحبال الحمراء في الملعب'], '1009434119_febe49276a': ['كلب أبيض وأسود يركض في حد

In [ ]:
!pip install tqdm

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
from keras.applications.xception import Xception
from tqdm import tqdm

def extract_features(directory):
        model = Xception( include_top=False, pooling='avg' )
        features = {}
        for img in tqdm(os.listdir(directory)):
            filename = directory + "/" + img
            image = Image.open(filename)
            image = image.resize((299,299))
            image = np.expand_dims(image, axis=0)
            image = preprocess_input(image)
            image = image/127.5
            image = image - 1.0
            feature = model.predict(image)
            features[img] = feature
        return features 
#2048 feature vector
features = extract_features(dataset_images)
dump(features, open("features.p","wb"))

In [ ]:
features = load(open("features.p","rb"))


In [ ]:
#load the data 
def load_photos(filename):
    file = load_doc(filename)
    photos = file.split("\n")[:-1]
    return photos
def load_clean_descriptions(filename, photos): 
    #loading clean_descriptions
    file = load_doc(filename)
    descriptions = {}
    for line in file.split("\n"):
        words = line.split()

        if len(words)<1 :
            continue
        image, image_caption = words[0]+".jpg", words[1:]
        if image in photos:
            if image not in descriptions:
                descriptions[image] = []
            desc = '<start> ' + " ".join(image_caption) + ' <end>'
            descriptions[image].append(desc)
    return descriptions
def load_features(photos):
    #loading all features
    all_features = load(open("features.p","rb"))
    #selecting only needed features
    features = {k: all_features[k] for k in photos}
    return features
filename = dataset_text + "/" + "Flickr_8k.trainImages.txt"
#train = loading_data(filename)
train_imgs = load_photos(filename)
train_descriptions = load_clean_descriptions("descriptions.txt", train_imgs)
print(train_descriptions)
train_features = load_features(train_imgs)


{'1000268201_693b08cb0e.jpg': ['<start> طفلة صغيرة تتسلق إلى مسرح خشبي <end>', '<start> طفلة صغيرة تتسلق الدرج إلى منزلها <end>', '<start> فتاة صغيرة في ثوب وردي تذهب إلى المقصورة الخشبية <end>'], '1001773457_577c3a7d70.jpg': ['<start> كلب أسود وكلب ثلاثي الألوان يلعبان مع بعضهما البعض على الطريق <end>', '<start> كلب أسود وكلب أبيض ببقع بنية يحدقان في بعضهما البعض في الشارع <end>', '<start> كلاب على الرصيف تتحرك نحو بعضها البعض <end>'], '1002674143_1b742ab4b8.jpg': ['<start> فتاة صغيرة مغطاة بالطلاء تجلس أمام قوس قزح <end>', '<start> فتاة صغيرة تجلس أمام قوس قزح ملون كبير <end>', '<start> فتاة أمام لوحة قوس قزح <end>'], '1003163366_44323f5815.jpg': ['<start> رجل يجلس على مقعد بينما يجلس كلبه بجانبه <end>', '<start> رجل ينام على مقعد في الخارج مع كلب أبيض وأسود يجلس بجانبه <end>', '<start> رجل بلا قميص يجلس على مقعد في الحديقة مع كلبه <end>'], '1007129816_e794419615.jpg': ['<start> رجل يرتدي قبعة برتقالية <end>', '<start> رجل يرتدي قبعة برتقالية ونظارات <end>', '<start> الرجل ذو الأذن ا

In [ ]:
#converting dictionary to clean list of descriptions
def dict_to_list(descriptions):
    print (descriptions)
    all_desc = []
    for key in descriptions.keys():
        [all_desc.append(d) for d in descriptions[key]]
    return all_desc
#creating tokenizer class 
#this will vectorise text corpus
#each integer will represent token in dictionary
from keras.preprocessing.text import Tokenizer
def create_tokenizer(descriptions):
    desc_list = dict_to_list(descriptions)
    tokenizer = Tokenizer()
    tokenizer.fit_on_texts(desc_list)
    return tokenizer
# give each word an index, and store that into tokenizer.p pickle file
tokenizer = create_tokenizer(train_descriptions)
dump(tokenizer, open('tokenizer.p', 'wb'))
vocab_size = len(tokenizer.word_index) + 1
vocab_size

{'1000268201_693b08cb0e.jpg': ['<start> طفلة صغيرة تتسلق إلى مسرح خشبي <end>', '<start> طفلة صغيرة تتسلق الدرج إلى منزلها <end>', '<start> فتاة صغيرة في ثوب وردي تذهب إلى المقصورة الخشبية <end>'], '1001773457_577c3a7d70.jpg': ['<start> كلب أسود وكلب ثلاثي الألوان يلعبان مع بعضهما البعض على الطريق <end>', '<start> كلب أسود وكلب أبيض ببقع بنية يحدقان في بعضهما البعض في الشارع <end>', '<start> كلاب على الرصيف تتحرك نحو بعضها البعض <end>'], '1002674143_1b742ab4b8.jpg': ['<start> فتاة صغيرة مغطاة بالطلاء تجلس أمام قوس قزح <end>', '<start> فتاة صغيرة تجلس أمام قوس قزح ملون كبير <end>', '<start> فتاة أمام لوحة قوس قزح <end>'], '1003163366_44323f5815.jpg': ['<start> رجل يجلس على مقعد بينما يجلس كلبه بجانبه <end>', '<start> رجل ينام على مقعد في الخارج مع كلب أبيض وأسود يجلس بجانبه <end>', '<start> رجل بلا قميص يجلس على مقعد في الحديقة مع كلبه <end>'], '1007129816_e794419615.jpg': ['<start> رجل يرتدي قبعة برتقالية <end>', '<start> رجل يرتدي قبعة برتقالية ونظارات <end>', '<start> الرجل ذو الأذن ا

9090

In [ ]:
#calculate maximum length of descriptions
def max_length(descriptions):
    desc_list = dict_to_list(descriptions)
    return max(len(d.split()) for d in desc_list)
    
max_length = max_length(descriptions)
max_length

{'1000268201_693b08cb0e': ['طفلة صغيرة تتسلق إلى مسرح خشبي', 'طفلة صغيرة تتسلق الدرج إلى منزلها', 'فتاة صغيرة في ثوب وردي تذهب إلى المقصورة الخشبية'], '1001773457_577c3a7d70': ['كلب أسود وكلب ثلاثي الألوان يلعبان مع بعضهما البعض على الطريق', 'كلب أسود وكلب أبيض ببقع بنية يحدقان في بعضهما البعض في الشارع', 'كلاب على الرصيف تتحرك نحو بعضها البعض'], '1002674143_1b742ab4b8': ['فتاة صغيرة مغطاة بالطلاء تجلس أمام قوس قزح', 'فتاة صغيرة تجلس أمام قوس قزح ملون كبير', 'فتاة أمام لوحة قوس قزح'], '1003163366_44323f5815': ['رجل يجلس على مقعد بينما يجلس كلبه بجانبه', 'رجل ينام على مقعد في الخارج مع كلب أبيض وأسود يجلس بجانبه', 'رجل بلا قميص يجلس على مقعد في الحديقة مع كلبه'], '1007129816_e794419615': ['رجل يرتدي قبعة برتقالية', 'رجل يرتدي قبعة برتقالية ونظارات', 'الرجل ذو الأذن المثقوبة يرتدي نظارات وقبعة برتقالية اللون'], '1007320043_627395c3d8': ['طفل يلعب على حبل', 'فتاة صغيرة تتسلق على الحبل الأحمر', 'طفل صغير يمسك بالحبال الحمراء في الملعب'], '1009434119_febe49276a': ['كلب أبيض وأسود يركض في حد

24

In [ ]:
i = 0
for k,v in train_descriptions.items():
    print(v)
    i += 1
    if i == 10: break

['<start> طفلة صغيرة تتسلق إلى مسرح خشبي <end>', '<start> طفلة صغيرة تتسلق الدرج إلى منزلها <end>', '<start> فتاة صغيرة في ثوب وردي تذهب إلى المقصورة الخشبية <end>']
['<start> كلب أسود وكلب ثلاثي الألوان يلعبان مع بعضهما البعض على الطريق <end>', '<start> كلب أسود وكلب أبيض ببقع بنية يحدقان في بعضهما البعض في الشارع <end>', '<start> كلاب على الرصيف تتحرك نحو بعضها البعض <end>']
['<start> فتاة صغيرة مغطاة بالطلاء تجلس أمام قوس قزح <end>', '<start> فتاة صغيرة تجلس أمام قوس قزح ملون كبير <end>', '<start> فتاة أمام لوحة قوس قزح <end>']
['<start> رجل يجلس على مقعد بينما يجلس كلبه بجانبه <end>', '<start> رجل ينام على مقعد في الخارج مع كلب أبيض وأسود يجلس بجانبه <end>', '<start> رجل بلا قميص يجلس على مقعد في الحديقة مع كلبه <end>']
['<start> رجل يرتدي قبعة برتقالية <end>', '<start> رجل يرتدي قبعة برتقالية ونظارات <end>', '<start> الرجل ذو الأذن المثقوبة يرتدي نظارات وقبعة برتقالية اللون <end>']
['<start> طفل يلعب على حبل <end>', '<start> فتاة صغيرة تتسلق على الحبل الأحمر <end>', '<start> طفل ص

In [ ]:
#create input-output sequence pairs from the image description.
#data generator, used by model.fit_generator()
def data_generator(descriptions, features, tokenizer, max_length):
  print (subset.items())
  while 1:
    for key, description_list in descriptions.items():
            #retrieve photo features
            feature = features[key][0]
            input_image, input_sequence, output_word = create_sequences(tokenizer, max_length, description_list, feature)
            yield [[input_image, input_sequence], output_word]
       
def create_sequences(tokenizer, max_length, desc_list, feature):
    X1, X2, y = list(), list(), list()
    # walk through each description for the image
    for desc in desc_list:
        # encode the sequence
        seq = tokenizer.texts_to_sequences([desc])[0]
        # split one sequence into multiple X,y pairs
        for i in range(1, len(seq)):
            # split into input and output pair
            in_seq, out_seq = seq[:i], seq[i]
            # pad input sequence
            in_seq = pad_sequences([in_seq], maxlen=max_length)[0]
            # encode output sequence
            out_seq = to_categorical([out_seq], num_classes=vocab_size)[0]
            # store
            X1.append(feature)
            X2.append(in_seq)
            y.append(out_seq)
    return np.array(X1), np.array(X2), np.array(y)
max_length=24
#You can check the shape of the input and output for your model
[a,b],c = next(data_generator(train_descriptions, features, tokenizer, max_length))
a.shape, b.shape, c.shape
#((47, 2048), (47, 32), (47, 7577))

dict_items([('1000268201_693b08cb0e', ['طفلة صغيرة تتسلق إلى مسرح خشبي', 'طفلة صغيرة تتسلق الدرج إلى منزلها', 'فتاة صغيرة في ثوب وردي تذهب إلى المقصورة الخشبية']), ('1001773457_577c3a7d70', ['كلب أسود وكلب ثلاثي الألوان يلعبان مع بعضهما البعض على الطريق', 'كلب أسود وكلب أبيض ببقع بنية يحدقان في بعضهما البعض في الشارع', 'كلاب على الرصيف تتحرك نحو بعضها البعض']), ('1002674143_1b742ab4b8', ['فتاة صغيرة مغطاة بالطلاء تجلس أمام قوس قزح', 'فتاة صغيرة تجلس أمام قوس قزح ملون كبير', 'فتاة أمام لوحة قوس قزح']), ('1003163366_44323f5815', ['رجل يجلس على مقعد بينما يجلس كلبه بجانبه', 'رجل ينام على مقعد في الخارج مع كلب أبيض وأسود يجلس بجانبه', 'رجل بلا قميص يجلس على مقعد في الحديقة مع كلبه']), ('1007129816_e794419615', ['رجل يرتدي قبعة برتقالية', 'رجل يرتدي قبعة برتقالية ونظارات', 'الرجل ذو الأذن المثقوبة يرتدي نظارات وقبعة برتقالية اللون']), ('1007320043_627395c3d8', ['طفل يلعب على حبل', 'فتاة صغيرة تتسلق على الحبل الأحمر', 'طفل صغير يمسك بالحبال الحمراء في الملعب']), ('1009434119_febe49276a', ['ك

((24, 2048), (24, 24), (24, 9090))

In [ ]:
from keras.utils import plot_model
# define the captioning model
def define_model(vocab_size, max_length):
    # features from the CNN model squeezed from 2048 to 256 nodes
    inputs1 = Input(shape=(2048,))
    fe1 = Dropout(0.5)(inputs1)
    fe2 = Dense(256, activation='relu')(fe1)
    # LSTM sequence model
    inputs2 = Input(shape=(max_length,))
    se1 = Embedding(vocab_size, 256, mask_zero=True)(inputs2)
    se2 = Dropout(0.5)(se1)
    se3 = LSTM(256)(se2)
    # Merging both models
    decoder1 = add([fe2, se3])
    decoder2 = Dense(256, activation='relu')(decoder1)
    outputs = Dense(vocab_size, activation='softmax')(decoder2)
    # tie it together [image, seq] [word]
    model = Model(inputs=[inputs1, inputs2], outputs=outputs)
    model.compile(loss='categorical_crossentropy', optimizer='adam')
    # summarize model
    print(model.summary())
    plot_model(model, to_file='model.png', show_shapes=True)
    return model

In [ ]:
# train our model
print('Dataset: ', len(train_imgs))
print('Descriptions: train=', len(train_descriptions))
print('Photos: train=', len(train_features))
print('Vocabulary Size:', vocab_size)
print('Description Length: ', max_length)
from keras.layers import add
import tensorflow as tf
model = define_model(vocab_size, max_length)
epochs = 10
steps = len(train_descriptions)
# making a directory models to save our models
#os.mkdir("models")
for i in range(epochs):
    generator = data_generator(train_descriptions, train_features, tokenizer, max_length)
    model.fit(generator, epochs=1, steps_per_epoch= steps, verbose=1)
    model.save("models/model_" + str(i) + ".h5")

Dataset:  6000
Descriptions: train= 6000
Photos: train= 6000
Vocabulary Size: 9090
Description Length:  24
Model: "model_2"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_6 (InputLayer)           [(None, 24)]         0           []                               
                                                                                                  
 input_5 (InputLayer)           [(None, 2048)]       0           []                               
                                                                                                  
 embedding_2 (Embedding)        (None, 24, 256)      2327040     ['input_6[0][0]']                
                                                                                                  
 dropout_4 (Dropout)            (None, 2048)         0           ['input_5[0][0]']  